In [1]:
import plotly.express as px
import pandas as pd
import numpy as np

from ostk.core.filesystem import Directory

from ostk.mathematics.geometry.d3.objects import Cuboid
from ostk.mathematics.geometry.d3.objects import Composite
from ostk.mathematics.geometry.d3.objects import Point

from ostk.physics import Environment
from ostk.physics.coordinate import Frame
from ostk.physics.environment.atmospheric import Earth as EarthAtmosphericModel
from ostk.physics.environment.gravitational import Earth as EarthGravitationalModel
from ostk.physics.environment.magnetic import Earth as EarthMagneticModel
from ostk.physics.environment.objects.celestial_bodies import Earth, Moon, Sun
from ostk.physics.time import DateTime, Duration, Instant, Scale, Time, Interval
from ostk.physics.units import Mass, Length, Angle

from ostk.astrodynamics.trajectory.state import NumericalSolver
from ostk.astrodynamics.trajectory.orbit.models.brouwerLyddaneMean import (
    BrouwerLyddaneMeanShort
)
from ostk.astrodynamics.trajectory import StateBuilder, State, Propagator
from ostk.astrodynamics.trajectory.state import CoordinatesBroker, CoordinatesSubset
from ostk.astrodynamics.trajectory.state.coordinates_subset import CartesianPosition, CartesianVelocity
from ostk.astrodynamics.trajectory import Orbit, Sequence
from ostk.astrodynamics import Dynamics
from ostk.astrodynamics.event_condition import LogicalCondition, RealCondition
from ostk.astrodynamics.dynamics import Thruster
from ostk.astrodynamics.flight.system import SatelliteSystem, PropulsionSystem
from ostk.astrodynamics.guidance_law import QLaw
from ostk.astrodynamics.solvers import FiniteDifferenceSolver
from ostk.astrodynamics.trajectory.orbit.models import Tabulated
from ostk.astrodynamics.trajectory.orbit.models.kepler import COE

## User inputs

In [6]:
earth = Earth.from_models(
    EarthGravitationalModel(EarthGravitationalModel.Type.EGM96, Directory.undefined(), 10, 10),
    EarthMagneticModel(EarthMagneticModel.Type.Undefined),
    EarthAtmosphericModel(EarthAtmosphericModel.Type.Undefined),
)

environment = Environment(Instant.J2000(), [earth])

In [7]:
mass = Mass.kilograms(200.0)
wet_mass = Mass.kilograms(14.0)
propulsion_system = PropulsionSystem(thrust_si_unit=1.0, specific_impulse_si_unit=1000.0)

## Setup environment, initial state and Satellite System

In [8]:
satellite_geometry = Composite(Cuboid(
    Point(0.0, 0.0, 0.0), np.eye(3).tolist(), [1.0, 0.0, 0.0]
))
satellite_system = SatelliteSystem(mass, satellite_geometry, np.eye(3), 2.0, 2.2, propulsion_system)

In [9]:
instant = Instant.date_time(DateTime(2024,10,1,0,0,0), Scale.UTC)
initial_state = Orbit.sun_synchronous(instant, Length.kilometers(585.0), Time(11, 0, 0), Earth.default()).get_state_at(instant)
coe = COE.cartesian((initial_state.get_position(), initial_state.get_velocity()), EarthGravitationalModel.EGM2008.gravitational_parameter)

In [10]:
coordinates_broker = CoordinatesBroker(
    [
        CartesianPosition.default(),
        CartesianVelocity.default(),
        CoordinatesSubset.mass()
    ]
)

state_builder = StateBuilder(
    frame=Frame.GCRF(),
    coordinates_subsets=[
        CartesianPosition.default(),
        CartesianVelocity.default(),
        CoordinatesSubset.mass()
    ],
)

coordinates = [
    *initial_state.get_coordinates().tolist(),
    mass.in_kilograms() + wet_mass.in_kilograms(),
]

propagation_state = state_builder.build(initial_state.get_instant(), coordinates)

In [11]:
numerical_solver = NumericalSolver(NumericalSolver.LogType.NoLog, NumericalSolver.StepperType.RungeKutta4, 15.0, 1e-12, 1e-12)

## SMA targeting

In [12]:
# Increasing the COE target SMA as it's osculating
target_coe = COE(
    coe.get_semi_major_axis() + Length.kilometers(5.0),
    coe.get_eccentricity(),
    coe.get_inclination(),
    coe.get_raan(),
    coe.get_aop(),
    coe.get_true_anomaly()
)

guidance_law = QLaw(
    target_coe,
    EarthGravitationalModel.EGM2008.gravitational_parameter,
    QLaw.Parameters(
        element_weights={COE.Element.SemiMajorAxis: 100.0},
        m=3,
        n=4,
        r=2,
        k=100,
        minimum_periapsis_radius=Length.kilometers(6575.0),
        b=0.01,
    ),
    QLaw.GradientStrategy.Analytical
)

In [13]:
dynamics = Dynamics.from_environment(environment) + [
    Thruster(
        satellite_system=satellite_system,
        guidance_law=guidance_law,
    )
]
propagator = Propagator(numerical_solver, dynamics)

In [14]:
end_state = propagator.calculate_state_at(propagation_state, propagation_state.get_instant() + Duration.hours(2.0))

In [17]:
data = []
for state in propagator.access_numerical_solver().get_observed_states():
    blmshort = BrouwerLyddaneMeanShort.cartesian((state.get_position(), state.get_velocity()), earth.get_gravitational_parameter())
    data.append(
        {
            "semi-major axis": float(blmshort.get_semi_major_axis().in_kilometers()),
            "time": state.get_instant().get_date_time(Scale.UTC)
        }
    )

df = pd.DataFrame(data)

In [18]:
fig = px.scatter(df, x="time", y="semi-major axis", title=f"Semi-Major Axis target: {target_coe.get_semi_major_axis().in_kilometers()}")
fig.show()

In [13]:
states = propagator.access_numerical_solver().get_observed_states()

In [14]:
accelerations = []
for s in states:
        acceleration = guidance_law.calculate_thrust_acceleration_at(s.get_instant(), s.get_position().get_coordinates(), s.get_velocity().get_coordinates(), 14.3e-3/s.get_coordinates()[6], Frame.GCRF())
        accelerations.append(dict(t=s.get_instant().get_date_time(Scale.UTC), pos_x=s.get_position().get_coordinates()[0], pos_y=s.get_position().get_coordinates()[1], pos_z=s.get_position().get_coordinates()[2], accel_x=acceleration[0], accel_y=acceleration[1], accel_z=acceleration[2]))

In [136]:
dfhax = pd.DataFrame(accelerations)

In [137]:
import plotly.graph_objects as go
import pandas as pd

# Assuming dfhax is your DataFrame with columns: 't', 'pos_x', 'pos_y', 'pos_z', 'accel_x', 'accel_y', 'accel_z'

# Create initial frame
fig = go.Figure(
    data=[
        go.Cone(
            x=[dfhax['pos_x'][0]], 
            y=[dfhax['pos_y'][0]], 
            z=[dfhax['pos_z'][0]],
            u=[dfhax['accel_x'][0]], 
            v=[dfhax['accel_y'][0]], 
            w=[dfhax['accel_z'][0]],
            sizemode='scaled', 
            sizeref=0.3, 
            colorscale='Viridis'
        )
    ],
    layout=go.Layout(
        scene=dict(
            xaxis_title='X Position',
            yaxis_title='Y Position',
            zaxis_title='Z Position'
        ),
        updatemenus=[dict(
            type="buttons",
            buttons=[dict(label="Play", method="animate", args=[None])]
        )]
    ),
    frames=[
        go.Frame(
            data=[
                go.Cone(
                    x=[dfhax['pos_x'][k]], 
                    y=[dfhax['pos_y'][k]], 
                    z=[dfhax['pos_z'][k]],
                    u=[dfhax['accel_x'][k]], 
                    v=[dfhax['accel_y'][k]], 
                    w=[dfhax['accel_z'][k]]
                )
            ],
            name=str(k)
        ) for k in range(len(dfhax))
    ]
)

# Update layout
fig.update_layout(
    title='Satellite Thrust Acceleration Vectors over Time (Animated)',
    scene=dict(
        xaxis_title='X Position',
        yaxis_title='Y Position',
        zaxis_title='Z Position'
    )
)

# Show the plot
fig.show()


### Eccentricity targeting

In [19]:
# Increasing the COE target SMA as it's osculating
target_coe = COE(
    coe.get_semi_major_axis(),
    coe.get_eccentricity() + 1e-3,
    coe.get_inclination(),
    coe.get_raan(),
    coe.get_aop(),
    coe.get_true_anomaly()
)
guidance_law = QLaw(
    target_coe,
    EarthGravitationalModel.EGM2008.gravitational_parameter,
    QLaw.Parameters(
        element_weights={COE.Element.Eccentricity: 1.0},
        m=3,
        n=4,
        r=2,
        k=100,
        minimum_periapsis_radius=Length.kilometers(6575.0),
        b=0.01,
    ),
    QLaw.GradientStrategy.Analytical,
)

In [20]:
dynamics = Dynamics.from_environment(environment) + [
    Thruster(
        satellite_system=satellite_system,
        guidance_law=guidance_law,
    )
]
propagator = Propagator(numerical_solver, dynamics)

In [21]:
end_state = propagator.calculate_state_at(propagation_state, propagation_state.get_instant() + Duration.hours(5.0))

In [24]:
data = []
for state in propagator.access_numerical_solver().get_observed_states():
    blmshort = BrouwerLyddaneMeanShort.cartesian((state.get_position(), state.get_velocity()), earth.get_gravitational_parameter())
    data.append(
        {
            "eccentricity": float(blmshort.get_eccentricity()),
            "time": state.get_instant().get_date_time(Scale.UTC)
        }
    )

df = pd.DataFrame(data)

In [25]:
fig = px.scatter(df, x="time", y="eccentricity", title=f"Eccentricity target {target_coe.get_eccentricity()}")
fig.show()

### Inclination targeting

In [26]:
# Increasing the COE target SMA as it's osculating
target_coe = COE(
    coe.get_semi_major_axis(),
    coe.get_eccentricity(),
    coe.get_inclination() + Angle.degrees(1e-1),
    coe.get_raan(),
    coe.get_aop(),
    coe.get_true_anomaly()
)
guidance_law = QLaw(
    target_coe,
    EarthGravitationalModel.EGM2008.gravitational_parameter,
    QLaw.Parameters(
        element_weights={COE.Element.Inclination: 1.0},
        m=3,
        n=4,
        r=2,
        k=100,
        minimum_periapsis_radius=Length.kilometers(6575.0),
        b=0.01,
    ),
    QLaw.GradientStrategy.Analytical
)

In [27]:
dynamics = Dynamics.from_environment(environment) + [
    Thruster(
        satellite_system=satellite_system,
        guidance_law=guidance_law,
    )
]
propagator = Propagator(numerical_solver, dynamics)

In [28]:
end_state = propagator.calculate_state_at(propagation_state, propagation_state.get_instant() + Duration.hours(5.0))

In [31]:
data = []
for state in propagator.access_numerical_solver().get_observed_states():
    blmshort = BrouwerLyddaneMeanShort.cartesian((state.get_position(), state.get_velocity()), earth.get_gravitational_parameter())
    data.append(
        {
            "inclination": float(blmshort.get_inclination().in_degrees()),
            "time": state.get_instant().get_date_time(Scale.UTC)
        }
    )

df = pd.DataFrame(data)

In [32]:
fig = px.scatter(df, x="time", y="inclination", title=f"Inclination target: {target_coe.get_inclination().in_degrees()}")
fig.show()

### Right Ascension of Ascending Node targeting

In [33]:
# Increasing the COE target SMA as it's osculating
target_coe = COE(
    coe.get_semi_major_axis(),
    coe.get_eccentricity(),
    coe.get_inclination(),
    coe.get_raan() - Angle.degrees(1e-1),
    coe.get_aop(),
    coe.get_true_anomaly()
)
guidance_law = QLaw(
    target_coe,
    EarthGravitationalModel.EGM2008.gravitational_parameter,
    QLaw.Parameters(
        element_weights={COE.Element.Raan: 1.0},
        m=3,
        n=4,
        r=2,
        k=100,
        minimum_periapsis_radius=Length.kilometers(6575.0),
        b=0.01,
    ),
    QLaw.GradientStrategy.Analytical
)

In [34]:
dynamics = Dynamics.from_environment(environment) + [
    Thruster(
        satellite_system=satellite_system,
        guidance_law=guidance_law,
    )
]
propagator = Propagator(numerical_solver, dynamics)

In [35]:
end_state = propagator.calculate_state_at(propagation_state, propagation_state.get_instant() + Duration.hours(15.0))

In [38]:
data = []
for state in propagator.access_numerical_solver().get_observed_states():
    blmshort = BrouwerLyddaneMeanShort.cartesian((state.get_position(), state.get_velocity()), earth.get_gravitational_parameter())
    data.append(
        {
            "right ascension of ascending node": float(blmshort.get_raan().in_degrees()),
            "time": state.get_instant().get_date_time(Scale.UTC)
        }
    )

df = pd.DataFrame(data)

In [39]:
fig = px.scatter(df, x="time", y="right ascension of ascending node", title=f"RAAN target: {target_coe.get_raan().in_degrees()}")
fig.show()

### Argument of Periapsis targeting

In [40]:
target_coe = COE(
    coe.get_semi_major_axis(),
    coe.get_eccentricity(),
    coe.get_inclination(),
    coe.get_raan(),
    coe.get_aop() + Angle.degrees(30.0),
    coe.get_true_anomaly()
)
guidance_law = QLaw(
    target_coe,
    EarthGravitationalModel.EGM2008.gravitational_parameter,
    QLaw.Parameters(
        element_weights={COE.Element.Aop: 1.0},
        m=3,
        n=4,
        r=2,
        k=100,
        minimum_periapsis_radius=Length.kilometers(6575.0),
        b=0.01,
        
    ),
    FiniteDifferenceSolver.default(),
)

TypeError: __init__(): incompatible constructor arguments. The following argument types are supported:
    1. ostk.astrodynamics.guidance_law.QLaw(target_coe: ostk.astrodynamics.trajectory.orbit.models.kepler.COE, gravitational_parameter: ostk.physics.units.Derived, parameters: ostk.astrodynamics.guidance_law.QLaw.Parameters, gradient_strategy: ostk.astrodynamics.guidance_law.QLaw.GradientStrategy = <GradientStrategy.FiniteDifference: 1>)

Invoked with: -- Classical Orbital Elements ----------------------------------------------------------------------
    Semi-major axis:                         6963137.0 [m]                            
    Eccentricity:                            0.0                                      
    Inclination:                             97.728513019047639 [deg]                 
    Right ascension of the ascending node:   354.93066948516838 [deg]                 
    Argument of periapsis:                   29.999999999999996 [deg]                 
    Tr

In [41]:
dynamics = Dynamics.from_environment(environment) + [
    Thruster(
        satellite_system=satellite_system,
        guidance_law=guidance_law,
    )
]
propagator = Propagator(numerical_solver, dynamics)

In [42]:
end_state = propagator.calculate_state_at(propagation_state, propagation_state.get_instant() + Duration.days(1.0))

In [43]:
data = []
for state in propagator.access_numerical_solver().get_observed_states():
    blmshort = COE.cartesian((state.get_position(), state.get_velocity()), earth.get_gravitational_parameter())
    data.append(
        {
            "argument of periapsis": float(blmshort.get_aop().in_degrees()),
            "time": state.get_instant().get_date_time(Scale.UTC)
        }
    )

df = pd.DataFrame(data)

In [44]:
fig = px.scatter(df, x="time", y="argument of periapsis", title=f"AOP target: {target_coe.get_aop().in_degrees()}")
fig.show()

## Multiple targets

### SMA + Ecc

In [47]:
# Increasing the COE target SMA as it's osculating
target_coe = COE(
    coe.get_semi_major_axis() + Length.kilometers(5.0),
    coe.get_eccentricity() + 0.001,
    coe.get_inclination(),
    coe.get_raan(),
    coe.get_aop(),
    coe.get_true_anomaly()
)
guidance_law = QLaw(
    target_coe,
    EarthGravitationalModel.EGM2008.gravitational_parameter,
    QLaw.Parameters(
        element_weights={COE.Element.SemiMajorAxis: 1.0, COE.Element.Eccentricity: 1.0},
        m=3,
        n=4,
        r=2,
        k=100,
        minimum_periapsis_radius=Length.kilometers(6575.0),
        b=0.01,
        
    ),
    QLaw.GradientStrategy.Analytical
)

dynamics = Dynamics.from_environment(environment) + [
    Thruster(
        satellite_system=satellite_system,
        guidance_law=guidance_law,
    )
]
propagator = Propagator(numerical_solver, dynamics)

In [48]:
end_state = propagator.calculate_state_at(propagation_state, propagation_state.get_instant() + Duration.hours(10.0))

In [49]:
data = []
for state in propagator.access_numerical_solver().get_observed_states():
    blmshort = BrouwerLyddaneMeanShort.cartesian((state.get_position(), state.get_velocity()), earth.get_gravitational_parameter())
    data.append(
        {
            "semi-major axis": float(blmshort.get_semi_major_axis().in_kilometers()),
            "eccentricity": float(blmshort.get_eccentricity()),
            "time": state.get_instant().get_date_time(Scale.UTC)
        }
    )

df = pd.DataFrame(data)

In [50]:
fig = px.scatter(df, x="time", y="semi-major axis", title=f"SMA target: {target_coe.get_semi_major_axis().in_kilometers()}")
fig.show()

In [51]:
fig = px.scatter(df, x="time", y="eccentricity", title=f"Eccentricity target: {target_coe.get_eccentricity()}")
fig.show()

### Semi Major Axis + Inclination

In [ ]:
# Increasing the COE target SMA as it's osculating
target_coe = COE(
    coe.get_semi_major_axis() + Length.kilometers(5.0),
    coe.get_eccentricity(),
    coe.get_inclination() + Angle.degrees(1e-1),
    coe.get_raan(),
    coe.get_aop(),
    coe.get_true_anomaly()
)
guidance_law = QLaw(
    target_coe,
    EarthGravitationalModel.EGM2008.gravitational_parameter,
    QLaw.Parameters(
        element_weights={COE.Element.SemiMajorAxis: 1.0, COE.Element.Inclination: 1.0},
        m=3,
        n=4,
        r=2,
        k=100,
        minimum_periapsis_radius=Length.kilometers(6575.0),
        b=0.01,
        
    ),
    FiniteDifferenceSolver.default(),
)

dynamics = Dynamics.from_environment(environment) + [
    Thruster(
        satellite_system=satellite_system,
        guidance_law=guidance_law,
    )
]
propagator = Propagator(numerical_solver, dynamics)

In [ ]:
end_state = propagator.calculate_state_at(propagation_state, propagation_state.get_instant() + Duration.days(10.0))

In [ ]:
data = []
for state in propagator.access_numerical_solver().get_observed_states():
    blmshort = COE.cartesian((state.get_position(), state.get_velocity()), earth.get_gravitational_parameter())
    data.append(
        {
            "semi-major axis": float(blmshort.get_semi_major_axis().in_kilometers()),
            "inclination": float(blmshort.get_inclination().in_degrees()),
            "time": state.get_instant().get_date_time(Scale.UTC)
        }
    )

df = pd.DataFrame(data)

In [ ]:
fig = px.scatter(df, x="time", y="semi-major axis", title=f"SMA target: {target_coe.get_semi_major_axis().in_kilometers()}")
fig.show()

In [ ]:
fig = px.scatter(df, x="time", y="inclination", title=f"Inclination target: {target_coe.get_inclination().in_degrees()}")
fig.show()

### SMA + Ecc + Inclination

In [172]:
target_coe = COE(
    coe.get_semi_major_axis() + Length.kilometers(5.0),
    coe.get_eccentricity() + 0.001,
    coe.get_inclination() + Angle.degrees(1e-1),
    coe.get_raan(),
    coe.get_aop(),
    coe.get_true_anomaly()
)
guidance_law = QLaw(
    target_coe,
    EarthGravitationalModel.EGM2008.gravitational_parameter,
    QLaw.Parameters(
        element_weights={COE.Element.SemiMajorAxis: 1.0, COE.Element.Eccentricity: 1.0, COE.Element.Inclination: 1.0},
        m=3,
        n=4,
        r=2,
        k=100,
        minimum_periapsis_radius=Length.kilometers(6575.0),
        b=0.01,
        
    ),
    FiniteDifferenceSolver.default(),
)

dynamics = Dynamics.from_environment(environment) + [
    Thruster(
        satellite_system=satellite_system,
        guidance_law=guidance_law,
    )
]
propagator = Propagator(numerical_solver, dynamics)

In [173]:
end_state = propagator.calculate_state_at(propagation_state, propagation_state.get_instant() + Duration.hours(10.0))

In [174]:
data = []
for state in propagator.access_numerical_solver().get_observed_states():
    blmshort = COE.cartesian((state.get_position(), state.get_velocity()), earth.get_gravitational_parameter())
    data.append(
        {
            "semi-major axis": float(blmshort.get_semi_major_axis().in_kilometers()),
            "eccentricity": float(blmshort.get_eccentricity()),
            "inclination": float(blmshort.get_inclination().in_degrees()),
            "time": state.get_instant().get_date_time(Scale.UTC)
        }
    )

df = pd.DataFrame(data)

In [175]:
fig = px.scatter(df, x="time", y="semi-major axis", title=f"SMA target: {target_coe.get_semi_major_axis().in_kilometers()}")
fig.show()

In [176]:
fig = px.scatter(df, x="time", y="eccentricity", title=f"Eccentricity target: {target_coe.get_eccentricity()}")
fig.show()

In [177]:
fig = px.scatter(df, x="time", y="inclination", title=f"Inclination target: {target_coe.get_inclination().in_degrees()}")
fig.show()

### SMA + Ecc + Inc + Raan targeting

In [53]:
target_coe = COE(
    coe.get_semi_major_axis() + Length.kilometers(5.0),
    coe.get_eccentricity() + 0.001,
    coe.get_inclination() + Angle.degrees(1e-1),
    coe.get_raan() - Angle.degrees(1e-1),
    coe.get_aop(),
    coe.get_true_anomaly()
)
guidance_law = QLaw(
    target_coe,
    EarthGravitationalModel.EGM2008.gravitational_parameter,
    QLaw.Parameters(
        element_weights={COE.Element.SemiMajorAxis: 1.0, COE.Element.Eccentricity: 1.0, COE.Element.Inclination: 1.0, COE.Element.Raan: 1.0},
        m=3,
        n=4,
        r=2,
        k=100,
        minimum_periapsis_radius=Length.kilometers(6575.0),
        b=0.01,
        
    ),
    QLaw.GradientStrategy.FiniteDifference
)

dynamics = Dynamics.from_environment(environment) + [
    Thruster(
        satellite_system=satellite_system,
        guidance_law=guidance_law,
    )
]
propagator = Propagator(numerical_solver, dynamics)

In [54]:
end_state = propagator.calculate_state_at(propagation_state, propagation_state.get_instant() + Duration.hours(10.0))

In [60]:
data = []
for state in propagator.access_numerical_solver().get_observed_states():
    blmshort = COE.cartesian((state.get_position(), state.get_velocity()), earth.get_gravitational_parameter())
    data.append(
        {
            "semi-major axis": float(blmshort.get_semi_major_axis().in_kilometers()),
            "eccentricity": float(blmshort.get_eccentricity()),
            "inclination": float(blmshort.get_inclination().in_degrees()),
            "right ascension of ascending node": float(blmshort.get_raan().in_degrees()),
            "time": state.get_instant().get_date_time(Scale.UTC)
        }
    )

df = pd.DataFrame(data)

In [61]:
fig = px.scatter(df, x="time", y="semi-major axis", title=f"SMA target: {target_coe.get_semi_major_axis().in_kilometers()}")
fig.show()

In [62]:
fig = px.scatter(df, x="time", y="eccentricity", title=f"Eccentricity target: {target_coe.get_eccentricity()}")
fig.show()

In [58]:
fig = px.scatter(df, x="time", y="inclination", title=f"Inclination target: {target_coe.get_inclination().in_degrees()}")
fig.show()

In [59]:
fig = px.scatter(df, x="time", y="right ascension of ascending node", title=f"RAAN target: {target_coe.get_raan().in_degrees()}")
fig.show()